In [1]:
# DATA LOADING

from utils.data_loader.mobility_data_loader import mobility_data_loader 

# Process whole dataset in to intermediate form
dataframe = mobility_data_loader('20240101','20240101')

1
20240101 dataframe shape
(85653, 18)


In [2]:
df = dataframe['20240101']

In [3]:
from utils.folium_mapper.ishikawa_region_mapper import ishikawa_region_mapper
map, jpn_adm2 = ishikawa_region_mapper()
# Drop rows where 'longitude_h' or 'latitude_h' is NA
df_with_homes = df.dropna(subset=['longitude_h', 'latitude_h'])
df_with_homes.shape

from utils.data_filter.data_travel_filter_by_region import data_travel_filter_by_region
df_travel_inside_study_area = data_travel_filter_by_region(df_with_homes, jpn_adm2)
df_travel_inside_study_area.shape

e:\IRP_noto_earthquake\.venv\lib\site-packages\IPython\core\interactiveshell.py:3577: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  exec(code_obj, self.user_global_ns, self.user_ns)
e:\IRP_noto_earthquake\.venv\lib\site-packages\IPython\core\interactiveshell.py:3577: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  exec(code_obj, self.user_global_ns, self.user_ns)


(2700, 22)

In [4]:
from utils.data_filter.data_home_filter_by_region import data_home_filter_by_region

df_home_and_travel_inside_study_area = data_home_filter_by_region(df_travel_inside_study_area, jpn_adm2, True)
df_home_and_travel_inside_study_area.shape

e:\IRP_noto_earthquake\.venv\lib\site-packages\IPython\core\interactiveshell.py:3577: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  exec(code_obj, self.user_global_ns, self.user_ns)


(1431, 22)

In [5]:
df_home_and_travel_inside_study_area.shape

(1431, 22)

In [6]:
import pandas as pd
# Filter data that only was after earthquake time

earthquake_time = pd.to_datetime('2024-01-01 16:10:00')

# Keep travels that only are after the earthquake
df_residents = df_home_and_travel_inside_study_area[df['depart_time_o'] < earthquake_time]
df_residents.shape

C:\Users\HP\AppData\Local\Temp\ipykernel_23012\4258563812.py:7: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df_residents = df_home_and_travel_inside_study_area[df['depart_time_o'] < earthquake_time]


(742, 22)

In [10]:
d = df_residents[:300]
d.shape

(300, 22)

In [11]:
import pandas as pd
import numpy as np
import plotly.express as px

# Create a DataFrame to hold hourly positions for each common_id
start_date = d['arrive_time_o'].min().normalize()
end_date = d['depart_time_d'].max().normalize() + pd.Timedelta(days=1)

hours = pd.date_range(start=start_date, end=end_date, freq='H')

rows = []

for _, row in d.iterrows():
    for hour in hours:
        if hour < row['arrive_time_o']:
            # Before arrival at origin
            continue
        elif row['arrive_time_o'] <= hour < row['depart_time_o']:
            # Stationary at origin
            lat = row['latitude_o']
            lon = row['longitude_o']
        elif row['depart_time_o'] <= hour < row['arrive_time_d']:
            # Moving from origin to destination
            total_move_time = (row['arrive_time_d'] - row['depart_time_o']).total_seconds()
            elapsed_time = (hour - row['depart_time_o']).total_seconds()
            fraction = elapsed_time / total_move_time
            lat = row['latitude_o'] + fraction * (row['latitude_d'] - row['latitude_o'])
            lon = row['longitude_o'] + fraction * (row['longitude_d'] - row['longitude_o'])
        elif row['arrive_time_d'] <= hour <= row['depart_time_d']:
            # Stationary at destination
            lat = row['latitude_d']
            lon = row['longitude_d']
        else:
            # After departure from destination
            continue
        
        rows.append({
            'common_id': row['common_id'],
            'latitude': lat,
            'longitude': lon,
            'time': hour
        })

# Create a new DataFrame from the rows
movement_df = pd.DataFrame(rows)

# Create the Plotly animation
fig = px.scatter_mapbox(
    movement_df,
    lat='latitude',
    lon='longitude',
    color='common_id',
    size_max=15,
    zoom=10,
    mapbox_style='open-street-map',
    animation_frame=movement_df['time'].dt.strftime('%Y-%m-%d %H:%M:%S')
)

# Remove the legend
fig.for_each_trace(lambda trace: trace.update(showlegend=False))

fig.update_layout(
    title_text='Movement of People from Origin to Destination',
    title_x=0.5,
    width=1200,  # Increase the width of the figure
    height=800,  # Increase the height of the figure
    mapbox=dict(
        bearing=0,
        center=dict(lat=37.0, lon=137.0),
        pitch=0,
        zoom=5
    )
)

fig.show()


C:\Users\HP\AppData\Local\Temp\ipykernel_23012\2839281051.py:9: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

